# Multi-modal RAG with LangChain

## SetUp

Install the dependencies you need to run the notebook.

In [ ]:
!sudo apt-get install poppler-utils tesseract-ocr libmagic-dev

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
The following additional packages will be installed:
  tesseract-ocr-eng tesseract-ocr-osd
The following NEW packages will be installed:
  libmagic-dev poppler-utils tesseract-ocr tesseract-ocr-eng tesseract-ocr-osd
0 upgraded, 5 newly installed, 0 to remove and 20 not upgraded.
Need to get 5,107 kB of archives.
After this operation, 16.7 MB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu jammy-updates/main amd64 libmagic-dev amd64 1:5.41-3ubuntu0.1 [105 kB]
Get:2 http://archive.ubuntu.com/ubuntu jammy-updates/main amd64 poppler-utils amd64 22.02.0-2ubuntu0.6 [186 kB]
Get:3 http://archive.ubuntu.com/ubuntu jammy/universe amd64 tesseract-ocr-eng all 1:4.00~git30-7274cfa-1.1 [1,591 kB]
Get:4 http://archive.ubuntu.com/ubuntu jammy/universe amd64 tesseract-ocr-osd all 1:4.00~git30-7274cfa-1.1 [2,990 kB]
Get:5 http://archive.ubuntu.com/ubuntu jammy/universe amd64 te

In [ ]:
# for linux
# %sudo apt-get install poppler-utils tesseract-ocr libmagic-dev

# for mac
# %brew install poppler tesseract libmagic

In [ ]:
%pip install -Uq "unstructured[all-docs]" pillow lxml pillow
%pip install -Uq chromadb tiktoken
%pip install -Uq langchain langchain-community langchain-openai langchain-groq
%pip install -Uq python_dotenv
%pip install -Uq langchain_openai

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 981.5/981.5 kB 13.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.2/48.2 kB 5.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 117.0/117.0 kB 10.9 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 244.3/244.3 kB 22.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 472.8/472.8 kB 35.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.8/48.8 kB 4.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.6/5.6 MB 77.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 112.5/112.5 kB 11.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 590.6/590.6 kB 38.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 523.4/523.4 kB 32.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.0/16.0 MB 87.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [ ]:
import os

# keys for the services we will use
os.environ["OPENAI_API_KEY"] = "sk-proj-.."
os.environ["LANGCHAIN_API_KEY"] = "lsv2_pt_.."
os.environ["LANGCHAIN_TRACING_V2"] = "false"
#os.environ["LANGCHAIN_ENDPOINT"] = "https://eu.smith.langchain.com/"#"https://api.smith.langchain.com"
#os.environ["LANGCHAIN_PROJECT"] = "langchain-multimodal"


## Extract the data

Extract the elements of the PDF that we will be able to use in the retrieval process. These elements can be: Text, Images, Tables, etc.

### Partition PDF tables, text, and images

In [ ]:
from unstructured.partition.pdf import partition_pdf

output_path = "/content/"
file_path = output_path + '2023-conocophillips-aim-proxy-statment.pdf'

# Reference: https://docs.unstructured.io/open-source/core-functionality/chunking
chunks = partition_pdf(
    filename=file_path,
    infer_table_structure=True,            # extract tables
    strategy="hi_res",                     # mandatory to infer tables

    extract_image_block_types=["Image"],   # Add 'Table' to list to extract image of tables
    # image_output_dir_path=output_path,   # if None, images and tables will saved in base64

    extract_image_block_to_payload=True,   # if true, will extract base64 for API usage

    chunking_strategy="by_title",          # or 'basic'
    max_characters=10000,                  # defaults to 500
    combine_text_under_n_chars=2000,       # defaults to 0
    new_after_n_chars=6000,

    # extract_images_in_pdf=True,          # deprecated
)


yolox_l0.05.onnx:   0%|          | 0.00/217M [00:00<?, ?B/s]

PDFPageCountError: Unable to get page count.
I/O Error: Couldn't open file '/content/2023-conocophillips-aim-proxy-statment.pdf': No such file or directory.


In [ ]:
# We get 2 types of elements from the partition_pdf function
set([str(type(el)) for el in chunks])

In [ ]:
# Each CompositeElement containes a bunch of related elements.
# This makes it easy to use these elements together in a RAG pipeline.

chunks[3].metadata.orig_elements

In [ ]:
for i, chunk in enumerate(chunks):
    print(f"Metadata: {vars(chunk.metadata)}")

Metadata: {'filetype': 'application/pdf', 'languages': ['eng'], 'last_modified': '2025-02-17T02:29:13', 'page_number': 1, 'orig_elements': [<unstructured.documents.elements.Image object at 0x79059810d110>, <unstructured.documents.elements.Title object at 0x790597c2ecd0>, <unstructured.documents.elements.Header object at 0x790598f37a50>, <unstructured.documents.elements.Title object at 0x790598f20d50>, <unstructured.documents.elements.Title object at 0x79059864afd0>, <unstructured.documents.elements.Title object at 0x790598f35910>, <unstructured.documents.elements.Title object at 0x790598f36310>, <unstructured.documents.elements.Title object at 0x790598f36ed0>, <unstructured.documents.elements.NarrativeText object at 0x790598f37f90>, <unstructured.documents.elements.NarrativeText object at 0x790598f37d50>, <unstructured.documents.elements.NarrativeText object at 0x790598f37c90>, <unstructured.documents.elements.Footer object at 0x790598f37850>, <unstructured.documents.elements.Title obj

In [ ]:
# This is what an extracted image looks like.
# It contains the base64 representation only because we set the param extract_image_block_to_payload=True

elements = chunks[3].metadata.orig_elements
chunk_images = [el for el in elements if 'Image' in str(type(el))]
chunk_images[0].to_dict()

In [ ]:
chunk_images

### Separate extracted elements into tables, text, and images

In [ ]:
# separate tables from texts
tables = []
texts = []

for chunk in chunks:
    if "Table" in str(type(chunk)):
        tables.append(chunk)

    if "CompositeElement" in str(type((chunk))):
        texts.append(chunk)

In [ ]:
# Get the images from the CompositeElement objects
def get_images_base64(chunks):
    images_b64 = []
    for chunk in chunks:
        if "CompositeElement" in str(type(chunk)):
            chunk_els = chunk.metadata.orig_elements
            for el in chunk_els:
                if "Image" in str(type(el)):
                    images_b64.append(el.metadata.image_base64)
    return images_b64

images = get_images_base64(chunks)

In [ ]:
images

['...']

In [ ]:
images[0]

'/9j/4AAQSkZJRgABAQAAAQABAAD/2wBDAAgGBgcGBQgHBwcJCQgKDBQNDAsLDBkSEw8UHRofHh0aHBwgJC4nICIsIxwcKDcpLDAxNDQ0Hyc5PTgyPC4zNDL/2wBDAQkJCQwLDBgNDRgyIRwhMjIyMjIyMjIyMjIyMjIyMjIyMjIyMjIyMjIyMjIyMjIyMjIyMjIyMjIyMjIyMjIyMjL/wAARCACGAagDASIAAhEBAxEB/8QAHwAAAQUBAQEBAQEAAAAAAAAAAAECAwQFBgcICQoL/8QAtRAAAgEDAwIEAwUFBAQAAAF9AQIDAAQRBRIhMUEGE1FhByJxFDKBkaEII0KxwRVS0fAkM2JyggkKFhcYGRolJicoKSo0NTY3ODk6Q0RFRkdISUpTVFVWV1hZWmNkZWZnaGlqc3R1dnd4eXqDhIWGh4iJipKTlJWWl5iZmqKjpKWmp6ipqrKztLW2t7i5usLDxMXGx8jJytLT1NXW19jZ2uHi4+Tl5ufo6erx8vP09fb3+Pn6/8QAHwEAAwEBAQEBAQEBAQAAAAAAAAECAwQFBgcICQoL/8QAtREAAgECBAQDBAcFBAQAAQJ3AAECAxEEBSExBhJBUQdhcRMiMoEIFEKRobHBCSMzUvAVYnLRChYkNOEl8RcYGRomJygpKjU2Nzg5OkNERUZHSElKU1RVVldYWVpjZGVmZ2hpanN0dXZ3eHl6goOEhYaHiImKkpOUlZaXmJmaoqOkpaanqKmqsrO0tba3uLm6wsPExcbHyMnK0tPU1dbX2Nna4uPk5ebn6Onq8vP09fb3+Pn6/9oADAMBAAIRAxEAPwD3+iiigAooooAKKKKACiiigAooooAKKKKACiiigAooooAKKKKAEpa5G88bx6LrsthrVnJawMc290uXSRffA4P5/wCPT213BeQLNbzRyxt0dGDA/iKlST0RtUoVKaUpLR7MnoozRVGIUUUUAFFFFABRRRQAUUUUAFJTJZo4I2l

#### Check what the images look like

In [ ]:
import base64
from IPython.display import Image, display

def display_base64_image(base64_code):
    # Decode the base64 string to binary
    image_data = base64.b64decode(base64_code)
    # Display the image
    display(Image(data=image_data))

display_base64_image(images[0])

## Summarize the data

Create a summary of each element extracted from the PDF. This summary will be vectorized and used in the retrieval process.

### Text and Table summaries

We don't need a multimodal model to generate the summaries of the tables and the text. I will use open source models available on Groq.

In [ ]:
%pip install -Uq langchain-groq

In [ ]:
from langchain_groq import ChatGroq
from langchain_core.prompts import ChatPromptTemplate
from langchain_core.output_parsers import StrOutputParser
from langchain_openai import ChatOpenAI


In [ ]:
# Prompt
prompt_text = """
You are an assistant tasked with summarizing tables and text.
Give a concise summary of the table or text. Context is "Presentation focused on Analyst and Investor meeting containing graphs, charts, text, numbers and visualization etc."

Respond only with the summary, no additionnal comment.
Do not start your message by saying "Here is a summary" or anything like that.
Just give the summary as it is.

Table or text chunk: {element}
"""
prompt = ChatPromptTemplate.from_template(prompt_text)

# Summary chain
model = ChatOpenAI(model="gpt-4o-mini")
summarize_chain = {"element": lambda x: x} | prompt | model | StrOutputParser()

In [ ]:
# Summarize text
text_summaries = summarize_chain.batch(texts, {"max_concurrency": 3})
print(len(text_summaries))
text_summaries


In [ ]:
# Summarize tables
tables_html = [table.metadata.text_as_html for table in tables]
table_summaries = summarize_chain.batch(tables_html, {"max_concurrency": 3})

### Image summaries

We will use gpt-4o-mini to produce the image summaries.

In [ ]:
!pip install -Uq langchain_openai

In [ ]:
from langchain_openai import ChatOpenAI

prompt_template = """Describe the image in detail. For context,
                  "Proxy statements outline various plans for the company to shareholders,
                  from the election of directors, to pay for executives, approval or amendment of equity plans,
                  and even shareholder-sponsored proposals should any be received.
                  Be specific about graphs, charts, visualization."""
messages = [
    (
        "user",
        [
            {"type": "text", "text": prompt_template},
            {
                "type": "image_url",
                "image_url": {"url": "data:image/jpeg;base64,{image}"},
            },
        ],
    )
]

prompt = ChatPromptTemplate.from_messages(messages)

chain = prompt | ChatOpenAI(model="gpt-4o-mini") | StrOutputParser()


image_summaries = chain.batch(images)

In [ ]:
len(image_summaries)

In [ ]:
image_summaries

In [ ]:
print(image_summaries[1])

## Load data and summaries to vectorstore

### Create the vectorstore

In [ ]:
import uuid
from langchain.vectorstores import Chroma
from langchain.storage import InMemoryStore
from langchain.schema.document import Document
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers.multi_vector import MultiVectorRetriever

# The vectorstore to use to index the child chunks
vectorstore = Chroma(collection_name="multi_modal_rag", embedding_function=OpenAIEmbeddings())

# The storage layer for the parent documents
store = InMemoryStore()
id_key = "doc_id"

# The retriever (empty to start)
retriever = MultiVectorRetriever(
    vectorstore=vectorstore,
    docstore=store,
    id_key=id_key,
)

### Load the summaries and link the to the original data

In [ ]:
text_summaries[0]

In [ ]:
type(texts)

In [ ]:
# Add texts
doc_ids = [str(uuid.uuid4()) for _ in texts]
summary_texts = [
    Document(page_content=summary, metadata={id_key: doc_ids[i]}) for i, summary in enumerate(text_summaries)
]
retriever.vectorstore.add_documents(summary_texts)
retriever.docstore.mset(list(zip(doc_ids, texts)))



In [ ]:
# Add tables
table_ids = [str(uuid.uuid4()) for _ in tables]
if table_summaries:
    summary_tables = [
        Document(page_content=summary, metadata={id_key: table_ids[i]}) for i, summary in enumerate(table_summaries)
    ]
    retriever.vectorstore.add_documents(summary_tables)
    retriever.docstore.mset(list(zip(table_ids, tables)))



In [ ]:
# Add image summaries
img_ids = [str(uuid.uuid4()) for _ in images]
summary_img = [
    Document(page_content=summary, metadata={id_key: img_ids[i]}) for i, summary in enumerate(image_summaries)
]
retriever.vectorstore.add_documents(summary_img)
retriever.docstore.mset(list(zip(img_ids, images)))


### Check retrieval

In [ ]:
# Retrieve
docs = retriever.invoke(
    "Tell me about Triple Mandate (Aligned to Business Realities"
)
for doc in docs:
    print(str(doc) + "\n\n" + "-" * 80)


In [ ]:
# Retrieve
docs = retriever.invoke(
    "Tell me about Foundational Principles"
)
for doc in docs:
    print(str(doc) + "\n\n" + "-" * 80)


## RAG pipeline

In [ ]:
from langchain_core.runnables import RunnablePassthrough, RunnableLambda
from langchain_core.messages import SystemMessage, HumanMessage
from langchain_openai import ChatOpenAI
from base64 import b64decode


def parse_docs(docs):
    """Split base64-encoded images and texts"""
    b64 = []
    text = []
    for doc in docs:
        try:
            b64decode(doc)
            b64.append(doc)
        except Exception as e:
            text.append(doc)
    return {"images": b64, "texts": text}


def build_prompt(kwargs):

    docs_by_type = kwargs["context"]
    user_question = kwargs["question"]

    context_text = ""
    if len(docs_by_type["texts"]) > 0:
        for text_element in docs_by_type["texts"]:
            context_text += text_element.text

    # construct prompt with context (including images)
    prompt_template = f"""
    Answer the question based only on the following context, which can include text, tables, and the below image.
    Context: {context_text}
    Question: {user_question}
    """

    prompt_content = [{"type": "text", "text": prompt_template}]

    if len(docs_by_type["images"]) > 0:
        for image in docs_by_type["images"]:
            prompt_content.append(
                {
                    "type": "image_url",
                    "image_url": {"url": f"data:image/jpeg;base64,{image}"},
                }
            )

    return ChatPromptTemplate.from_messages(
        [
            HumanMessage(content=prompt_content),
        ]
    )


chain = (
    {
        "context": retriever | RunnableLambda(parse_docs),
        "question": RunnablePassthrough(),
    }
    | RunnableLambda(build_prompt)
    | ChatOpenAI(model="gpt-4o-mini")
    | StrOutputParser()
)

chain_with_sources = {
    "context": retriever | RunnableLambda(parse_docs),
    "question": RunnablePassthrough(),
} | RunnablePassthrough().assign(
    response=(
        RunnableLambda(build_prompt)
        | ChatOpenAI(model="gpt-4o-mini")
        | StrOutputParser()
    )
)

In [ ]:
response = chain.invoke(
    "Tell me about Triple Mandate (Aligned to Business Realities)"
)

print(response)

In [ ]:
response = chain_with_sources.invoke(
    "Tell me about Foundational Principles"
)

print("Response:", response['response'])

In [ ]:
# response = chain_with_sources.invoke(
#     "Tell me about Foundational Principles"
# )

# print("Response:", response['response'])

print("\n\nContext:")
for text in response['context']['texts']:
    print(text.text)
    print("Page number: ", text.metadata.page_number)
    print("\n" + "-"*50 + "\n")
for image in response['context']['images']:
    display_base64_image(image)

##Save

Saved the vectors etc


In [ ]:
# Check if variables exist and have content
print("Checking variables:")
print(f"vectorstore exists: {'vectorstore' in locals()}")
print(f"doc_ids exists: {'doc_ids' in locals()}")
print(f"table_ids exists: {'table_ids' in locals()}")
print(f"img_ids exists: {'img_ids' in locals()}")
print(f"texts exists: {'texts' in locals()}")
print(f"tables exists: {'tables' in locals()}")
print(f"images exists: {'images' in locals()}")
print(f"text_summaries exists: {'text_summaries' in locals()}")
print(f"table_summaries exists: {'table_summaries' in locals()}")
print(f"image_summaries exists: {'image_summaries' in locals()}")

Checking variables:
vectorstore exists: True
doc_ids exists: True
table_ids exists: False
img_ids exists: True
texts exists: True
tables exists: True
images exists: True
text_summaries exists: True
table_summaries exists: True
image_summaries exists: True


In [ ]:
print("\nChecking vectorstore:")
print(f"Type of vectorstore: {type(vectorstore)}")


Checking vectorstore:
Type of vectorstore: <class 'langchain_community.vectorstores.chroma.Chroma'>


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
# First, mount Google Drive if not already mounted


def save_complete_data_to_drive(vectorstore,
                              doc_ids, table_ids, img_ids,
                              texts, tables, images,
                              text_summaries, table_summaries, image_summaries,
                              drive_path="/content/drive/MyDrive/BI_RAG_Retriever/Presentation"):
    import os
    import pickle
    from langchain.vectorstores import Chroma

    # Create directory if it doesn't exist
    os.makedirs(drive_path, exist_ok=True)

    # Save all the data and their summaries
    saved_data = {
        # IDs
        'doc_ids': doc_ids,
        'table_ids': table_ids,
        'img_ids': img_ids,

        # Original content
        'texts': texts,
        'tables': tables,
        'images': images,

        # Summaries
        'text_summaries': text_summaries,
        'table_summaries': table_summaries,
        'image_summaries': image_summaries
    }

    # Create a new Chroma instance with the specified path
    new_vectorstore = Chroma(
        persist_directory=drive_path,
        embedding_function=vectorstore._embedding_function,
        collection_name="multi_modal_rag"
    )

    # Copy the collections from the original vectorstore
    new_vectorstore._collection = vectorstore._collection

    # Persist the new vectorstore
    new_vectorstore.persist()

    # Save all other data
    with open(os.path.join(drive_path, 'Presentation.pkl'), 'wb') as f:
        pickle.dump(saved_data, f)

    print(f"Saved complete data to Google Drive at {drive_path}")


# Usage example:
# To save everything to Google Drive:
save_complete_data_to_drive(vectorstore,
                          doc_ids, table_ids, img_ids,
                          texts, tables, images,
                          text_summaries, table_summaries, image_summaries)

Saved complete data to Google Drive at /content/drive/MyDrive/BI_RAG_Retriever/17Feb


<ipython-input-40-40d880e7fad7>:45: LangChainDeprecationWarning: Since Chroma 0.4.x the manual persistence method is no longer supported as docs are automatically persisted.
  new_vectorstore.persist()


##Load

In [ ]:


def load_complete_data(save_directory="/content/drive/MyDrive/BI_RAG_Retriever/Presentation"):
    import pickle
    import os
    from langchain.vectorstores import Chroma
    from langchain.storage import InMemoryStore
    from langchain.embeddings import OpenAIEmbeddings
    from langchain.retrievers.multi_vector import MultiVectorRetriever
    from langchain.schema.document import Document

    # Check if the path exists
    if not os.path.exists(drive_path):
        raise FileNotFoundError(f"Could not find saved data at {drive_path}. Please check if the path is correct.")

    # Load the vectorstore from Google Drive
    vectorstore = Chroma(
        persist_directory=drive_path,
        embedding_function=OpenAIEmbeddings(),
        collection_name="multi_modal_rag"
    )

    # Load the stored data
    with open(os.path.join(drive_path, 'test_presentation_part2_feb17.pkl'), 'rb') as f:
        saved_data = pickle.load(f)

    # Create the storage layer and retriever
    store = InMemoryStore()

    # Initialize the retriever
    retriever = MultiVectorRetriever(
        vectorstore=vectorstore,
        docstore=store,
        id_key="doc_id",
    )

    # Add text summaries to vectorstore
    summary_texts = [
        Document(page_content=summary, metadata={"doc_id": saved_data['doc_ids'][i]})
        for i, summary in enumerate(saved_data['text_summaries'])
    ]
    retriever.vectorstore.add_documents(summary_texts)

    # Add table summaries to vectorstore
    summary_tables = [
        Document(page_content=summary, metadata={"doc_id": saved_data['table_ids'][i]})
        for i, summary in enumerate(saved_data['table_summaries'])
    ]
    retriever.vectorstore.add_documents(summary_tables)

    # Add image summaries to vectorstore
    summary_img = [
        Document(page_content=summary, metadata={"doc_id": saved_data['img_ids'][i]})
        for i, summary in enumerate(saved_data['image_summaries'])
    ]
    retriever.vectorstore.add_documents(summary_img)

    # Restore the connections between summaries and original content
    retriever.docstore.mset(list(zip(saved_data['doc_ids'], saved_data['texts'])))
    retriever.docstore.mset(list(zip(saved_data['table_ids'], saved_data['tables'])))
    retriever.docstore.mset(list(zip(saved_data['img_ids'], saved_data['images'])))

    print(f"Loaded complete data from Google Drive at {drive_path}")

    return retriever, saved_data

# Usage example:
# To save everything to Google Drive:
save_complete_data_to_drive(vectorstore,
                          doc_ids, table_ids, img_ids,
                          texts, tables, images,
                          text_summaries, table_summaries, image_summaries)

# To load in a new session:
# First mount Google Drive
drive.mount('/content/drive')
# Then load the data
retriever, saved_data = load_complete_data_from_drive()

# Recreate the chain with the loaded retriever
chain_with_sources = {
    "context": retriever | RunnableLambda(parse_docs),
    "question": RunnablePassthrough(),
} | RunnablePassthrough().assign(
    response=(
        RunnableLambda(build_prompt)
        | ChatOpenAI(model="gpt-4o-mini")
        | StrOutputParser()
    )
)

# Now you can ask questions:
response = chain_with_sources.invoke("Who is the Lead Director?")
response = chain_with_sources.invoke("Who is the Lead Director?")
print("Response:", response['response'])